In [1]:
import pandas as pd
import numpy as np
from tqdm import tqdm
from scipy.special import softmax

from utils.model_utils import *


In [3]:
# reading in needed data files
gen_scores = pd.read_csv('data/genome-scores.csv')
ratings = pd.read_csv('data/ratings.csv')

In [4]:
# limiting data
ratings, movie_dict = set_up_ratings(ratings, min_move = 2000)

# print how many movies are being considers
print('toal movies being considered:', len(set(ratings['movieId'])))

toal movies being considered: 2428


In [5]:
gen_scores['movieId'] = gen_scores['movieId'].apply(lambda i: movie_dict.get(i, -1))
q, opt, rewards, steps = q_learning_v2(5000, ratings, gen_scores)

pd.DataFrame(q).to_csv('data/newqtable4.csv')
pd.DataFrame(opt).to_csv('data/new_policy4.csv')
pd.DataFrame(np.array(rewards)).to_csv('data/rewards4.csv')
pd.DataFrame(np.array(steps)).to_csv('data/steps4.csv')


  0%|          | 11/5000 [00:35<4:29:22,  3.24s/it]


KeyboardInterrupt: 

In [3]:
ratings = pd.read_csv('ratings.csv')
ratings.head()

userId  movieId  rating   timestamp
0       1      296     5.0  1147880044
1       1      306     3.5  1147868817
2       1      307     5.0  1147868828
3       1      665     5.0  1147878820
4       1      899     3.5  1147868510

In [4]:
def set_up_ratings(ratings, min_move=1000, min_use=50):

    by_movie = ratings.groupby('movieId').count()
    by_user = ratings.groupby('userId').count()

    by_movie = by_movie.reset_index()[['movieId', 'rating']]
    by_movie = by_movie[by_movie['rating']>=min_move]

    by_user = by_user.reset_index()[['userId', 'rating']]
    by_user = by_user[by_user['rating']>=min_use]

    all_movies = by_movie['movieId']
    movie_dict = dict(zip(all_movies, range(len(all_movies))))

    ratings = ratings[ratings['movieId'].isin(by_movie['movieId'])]
    ratings = ratings[ratings['userId'].isin(by_user['userId'])]

    ratings['movieId'] = ratings['movieId'].map(movie_dict)

    return ratings

ratings, movie_dict = set_up_ratings(ratings)


(3794, 2)
(102492, 2)


In [6]:
# TODO: change this file path
tags = pd.read_csv("tags.csv")

# Drop rows with NaN values in the 'tag' column
tags.dropna(subset=['tag'], inplace=True)

# Convert 'tag' column to strings
tags['tag'] = tags['tag'].astype(str)
movie_tags_df = tags.groupby('movieId')['tag'].agg(lambda x: ', '.join(x)).reset_index()
print(movie_tags_df)

       movieId                                                tag
0            1  Owned, imdb top 250, Pixar, Pixar, time travel...
1            2  Robin Williams, time travel, fantasy, based on...
2            3  funny, best friend, duringcreditsstinger, fish...
3            4  based on novel or book, chick flick, divorce, ...
4            5  aging, baby, confidence, contraception, daught...
...        ...                                                ...
45246   208813                                         might like
45247   208933               black and white, deal with the devil
45248   209035  computer animation, Japan, mass behavior, mass...
45249   209037  chameleon, computer animation, gluttony, humor...
45250   209063  black, education, friends schools, independent...

[45251 rows x 2 columns]


In [7]:
gen_tags = pd.read_csv('genome-tags.csv')
gen_scores = pd.read_csv('genome-scores.csv')

In [16]:
gen_scores.columns

Index(['movieId', 'tagId', 'relevance'], dtype='object')

In [100]:
len(set(gen_scores['movieId']))

13816

In [9]:
grouped = gen_scores.groupby('movieId').apply(lambda x: x.nlargest(25, 'relevance')).reset_index(drop=True)

# Create a dictionary where keys are movieId and values are lists of top 25 tagId by relevance
movie_tag_dict = {}
for movie_id, data in grouped.groupby('movieId'):
    movie_tag_dict[movie_id] = data['tagId'].tolist()

print(movie_tag_dict)

{1: [1036, 244, 786, 589, 64, 588, 785, 204, 186, 63, 536, 412, 971, 469, 203, 1062, 29, 310, 742, 414, 603, 717, 445, 278, 309], 2: [29, 204, 377, 588, 951, 584, 378, 415, 203, 62, 374, 107, 604, 132, 1074, 445, 742, 414, 646, 245, 623, 882, 355, 113, 867], 3: [901, 451, 902, 230, 742, 481, 863, 299, 464, 264, 445, 777, 1071, 1070, 646, 415, 374, 865, 417, 195, 188, 654, 807, 452, 971], 4: [1116, 201, 313, 439, 864, 846, 613, 742, 1062, 28, 388, 328, 967, 1035, 913, 545, 107, 412, 196, 195, 21, 646, 807, 1003, 425], 5: [901, 451, 383, 902, 808, 650, 374, 230, 768, 388, 742, 387, 900, 417, 1102, 1035, 299, 439, 849, 524, 807, 279, 1033, 464, 195], 6: [268, 498, 105, 465, 19, 481, 536, 241, 1085, 1020, 846, 841, 553, 195, 128, 240, 1089, 365, 468, 612, 424, 857, 302, 981, 323], 7: [849, 864, 865, 863, 613, 109, 450, 299, 769, 742, 614, 201, 846, 439, 490, 646, 445, 188, 334, 374, 1040, 603, 777, 302, 128], 8: [107, 22, 21, 605, 113, 29, 203, 309, 867, 374, 153, 152, 154, 742, 439, 204, 

In [6]:
movie_tags_df.loc[0, 'tag']

"Owned, imdb top 250, Pixar, Pixar, time travel, children, comedy, funny, witty, rated-G, animation, Pixar, computer animation, good cartoon chindren, pixar, friendship, bright, DARING RESCUES, fanciful, HEROIC MISSION, humorous, light, rousing, TOYS COME TO LIFE, UNLIKELY FRIENDSHIPS, warm, witty, animation, Disney, friendship, pixar, boy, boy next door, bullying, friends, friendship, jealousy, martial arts, mission, neighborhood, new toy, pixar, rescue, resourcefulness, rivalry, toy, toy comes to life, walkie talkie, clever, animation, clever, friendship, funny, Tom Hanks, witty, pixar, Pixar, toys, animation, fun, children, pixar, Tom Hanks, dolls, National Film Registry, adventure, animated, animation, cgi, comedy, Disney, family, fantasy, friendship, imdb top 250, Pixar, Tom Hanks, witty, classic, pixar, witty, Pixar, funny, animated, comedy, Disney, fun, funny, pixar, animated, animation, children, comedy, fantasy, funny, humorous, Pixar, time travel, Pixar, Pixar, Tom Hanks, ani

In [10]:
# Create a dictionary mapping movie IDs to sets of tags
movie_tags_dict = {}
tag_encoding_dict={}

for index, row in movie_tags_df.iterrows():
    movie_id = row['movieId']
    tag_encodings = set()
    tags = set(row['tag'].split(', '))
    for tag in tags:
        if tag not in tag_encoding_dict:
            encoding = len(tag_encoding_dict)
            tag_encoding_dict[tag] = encoding
        else:
            encoding = tag_encoding_dict[tag]
        tag_encodings.add(encoding)
    movie_tags_dict[movie_id] = tag_encodings

In [11]:
def count_similar_encodings(encodings1, encodings2):
    # Count the number of similar encodings
    num_similar_encodings = len(encodings1.intersection(encodings2))
    
    return num_similar_encodings

In [105]:
def calculate_similarity(list1, list2):
    if len(list1) != len(list2):
        raise ValueError("Lists must be of equal length")

    similarity_score = 0
    for i in range(len(list1)):
        similarity_score += abs(list1[i] - list2[i]) * 50

    return similarity_score / len(list1)    

In [135]:
by_mov = ratings.groupby('movieId').mean()['rating']

for i in by_mov:
    print(i)

3.8825560020519836
3.228283732378608
3.0868112543962485
2.82492453643812
3.011544772620722
3.862387505356888
3.3346183081767835
3.103585657370518
2.9131267409470754
3.4069036286625036
3.637705028233396
2.5775523560209423
3.3137254901960786
3.41476846057572
2.702187853640136
3.8287045279211918
3.935174304739522
3.367731629392971
2.6250545613269316
2.8470505617977526
3.554387351778656
3.3134025540040577
3.1252879447146147
3.1823662396382817
3.6814973063347574
3.5667141500474835
3.3770987239758226
4.010512232415902
3.937416062315337
3.588855421686747
3.230886655641776
3.9275129850290256
3.5631821443407983
3.4440789473684212
3.904468764249886
3.4056567222006975
3.8316398532317244
3.05
3.4190913731495662
2.660594288114238
3.389047680914642
3.25046176579239
4.080747178740444
2.9756035144587565
4.281851771354053
3.52060785767235
3.320203892493049
3.9440228884189574
3.090527119938885
3.2200496585971448
3.648266589141653
3.047479197258933
2.737785016286645
2.2872741978970073
2.0259341885108757


In [160]:
def q_learning_v2(num_episodes, ratings, gen_scores):

    movies = list(set(ratings['movieId']))
    reward_dict= {0.5:-25, 1:-20, 1.5:-15, 2:-10, 2.5:-5, 3:0, 3.5:5, 4:10, 4.5:15, 5:25}

    Q = np.zeros((len(movies), len(movies)))
    by_mov = ratings.groupby('movieId').mean()['rating']
    for i in tqdm(range(Q.shape[1])):
        Q[:, i] = by_mov[i]*8-25  
        # tags_mov = list(gen_scores[gen_scores['movieId']==i]['relevance'])
        # for j in range(Q.shape[0]):
        #     tags_2 = list(gen_scores[gen_scores['movieId']==j]['relevance'])
        #     if tags_mov and tags_2:
        #         Q[j, i] += calculate_similarity(tags_mov, tags_2)


    num_updates = np.zeros((len(movies), len(movies)))

    gamma = 0.5
    epsilon = 0.9

    # set up optimal policy array and list of checkpoint values
    optimal_policy = np.random.choice(a = movies, size=(len(movies)))

    for i in tqdm(range(num_episodes)):

        # reset environment and variables before each episode
        observation = ratings.sample(n=1)
        terminated = False
        reward = 0
        num_steps = 0
        prev_actions = []

        mov = observation['movieId'].values[0]

        pos_actions = np.array(list(ratings[ratings['userId']==observation['userId'].values[0]]['movieId']))
        tags_mov = list(gen_scores[gen_scores['movieId']==mov]['relevance'])
        for j in pos_actions:
            if not num_updates[mov, j]:
                num_updates[mov, j] = 1
                tags_2 = list(gen_scores[gen_scores['movieId']==j]['relevance'])
                if tags_mov and tags_2:
                    Q[observation['movieId'].values[0], j] += calculate_similarity(tags_mov, tags_2)

      
        # until episode is terminated keep exploring
        while not terminated:

            # get possible actions and then choose action using possible actions, random number and epsilon value
            pos_actions = [j for j in pos_actions if j not in prev_actions]

            # calculate reward based on reviews and movie similarities
            mov = observation['movieId'].values[0]

            if np.random.rand()< epsilon:
                probs = softmax(Q[mov, pos_actions])
                action = int(np.random.choice(a = pos_actions, p = probs)) 
            else:
                maxi = np.argmax(Q[observation['movieId'].values[0], pos_actions])
                action = pos_actions[maxi]
            prev_actions += [action]


            new_state = ratings[(ratings['userId'] == observation['userId'].values[0]) & (ratings['movieId'] == action)]
            if new_state.empty:
                continue


   
    
            # if tags_mov and tags_action:
            #     # similarity_score = count_similar_encodings(set(tags_mov), set(tags_action))
            #     similarity_score = calculate_similarity(tags_mov, tags_action)
            # else:
            #     similarity_score = 0
            reward = reward_dict[new_state['rating'].values[0]] 
            # + similarity_score

            # calculate eta then update matrices correctly using Q-learning equation
            num_updates[mov, action] += 1
            eta = 1/(1+num_updates[mov, action])
            # print(reward)
            Q[mov, action] = (1-eta)*Q[mov, action]+eta*(reward+gamma*np.max(Q[action,:]))


            # update optimal policy from new information
            optimal_policy[mov] = int(np.argmax(Q[mov,:]))

            observation = new_state
            num_steps += 1

            if reward < 10  or num_steps >20:
                terminated = True

        # update epsilon after each episode
        epsilon *= .9999

        # change optimal policy to ints
        optimal_policy = optimal_policy.astype(int)

    return Q, optimal_policy


In [161]:
q2, opt2 = q_learning_v2(4000, ratings, gen_scores)

 18%|█▊        | 726/4000 [1:56:28<6:50:53,  7.53s/it] 

In [108]:
def q_learning(num_episodes, ratings, gen_scores):

    movies = list(set(ratings['movieId']))
    reward_dict= {0.5:-25, 1:-20, 1.5:-15, 2:-10, 2.5:-5, 3:0, 3.5:5, 4:10, 4.5:15, 5:25}

    Q = np.zeros((len(movies), len(movies)))
    num_updates = np.zeros((len(movies), len(movies)))

    gamma = 0.9
    epsilon = 0.9

    # set up optimal policy array and list of checkpoint values
    optimal_policy = np.random.choice(a = movies, size=(len(movies)))

    for i in tqdm(range(num_episodes)):

        # reset environment and variables before each episode
        observation = ratings.sample(n=1)
        terminated = False
        reward = 0
        num_steps = 0
        prev_actions = []
      
        # until episode is terminated keep exploring
        while not terminated:

            # get possible actions and then choose action using possible actions, random number and epsilon value
            pos_actions = np.array(list(ratings[ratings['userId']==observation['userId'].values[0]]['movieId']))
            pos_actions = [i for i in pos_actions if i not in prev_actions]

            if np.random.rand()< epsilon:
                action = int(np.random.choice(a = pos_actions)) 
            else:
                maxi = np.argmax(Q[observation['movieId'].values[0], pos_actions])
                action = pos_actions[maxi]
            prev_actions += [action]


            new_state = ratings[(ratings['userId'] == observation['userId'].values[0]) & (ratings['movieId'] == action)]
            if new_state.empty:
                continue

            # calculate reward based on reviews and movie similarities
            mov = observation['movieId'].values[0]
            # tags_mov = movie_tag_dict.get(mov)
            # tags_action = movie_tag_dict.get(action)
            tags_mov = list(gen_scores[gen_scores['movieId']==mov]['relevance'])
            tags_action = list(gen_scores[gen_scores['movieId']==action]['relevance'])
            if tags_mov and tags_action:
                # similarity_score = count_similar_encodings(set(tags_mov), set(tags_action))
                similarity_score = calculate_similarity(tags_mov, tags_action)
            else:
                similarity_score = 0
            reward = reward_dict[new_state['rating'].values[0]] + similarity_score

            # calculate eta then update matrices correctly using Q-learning equation
            eta = 1/(1+num_updates[mov, action])
            # print(reward)
            Q[mov, action] = (1-eta)*Q[mov, action]+eta*(reward+gamma*np.max(Q[mov,:]))
            num_updates[mov, action] += 1


            # update optimal policy from new information
            optimal_policy[mov] = int(np.argmax(Q[mov,:]))

            observation = new_state
            num_steps += 1

            if reward < 10  or num_steps >20:
                terminated = True

        # update epsilon after each episode
        epsilon *= .9999

        # change optimal policy to ints
        optimal_policy = optimal_policy.astype(int)

    return Q, optimal_policy


In [42]:
q10k = Q
opt10k = optimal_policy

In [109]:
Q, optimal_policy = q_learning(10000, ratings, gen_scores)

100%|██████████| 10000/10000 [7:10:36<00:00,  2.58s/it]    


In [110]:
Q.to_csv('10k_with_genomes_q.csv')

AttributeError: 'numpy.ndarray' object has no attribute 'to_csv'

In [111]:
Q = pd.DataFrame(Q)
Q.to_csv('10_k_with_genome_Q.csv')

In [112]:
opt_pol = pd.DataFrame(optimal_policy)
opt_pol.to_csv('10_k_with_genome_pol.csv')

In [113]:
Q.head()

0           1     2     3           4           5     6     7     8     \
0   0.0  212.658060   0.0   0.0  210.399170  223.030957   0.0   0.0   0.0   
1   0.0    0.000000   0.0   0.0    0.000000    0.000000   0.0   0.0   0.0   
2   0.0    0.000000   0.0   0.0    0.000000   64.696030   0.0   0.0   0.0   
3   0.0   15.127704   0.0   0.0   57.654076    0.000000   0.0   0.0   0.0   
4   0.0    0.000000   0.0   0.0    0.000000    0.000000   0.0   0.0   0.0   

         9     ...        3784  3785        3786  3787  3788  3789       3790  \
0    0.000000  ...  222.082953   0.0    0.000000   0.0   0.0   0.0    0.00000   
1  289.356771  ...    0.000000   0.0  288.023635   0.0   0.0   0.0  268.13165   
2    0.000000  ...    0.000000   0.0    0.000000   0.0   0.0   0.0    0.00000   
3    0.000000  ...    0.000000   0.0    0.000000   0.0   0.0   0.0    0.00000   
4    0.000000  ...    0.000000   0.0    0.000000   0.0   0.0   0.0    0.00000   

   3791  3792  3793  
0   0.0   0.0   0.0  
1   0.0   0.0   0.0  
2   0.0   0.0   0.0  
3   0.0   0.0   0.0  
4   0.0   0.0   0.0  

[5 rows x 3794 columns]

In [78]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import OneHotEncoder
from keras.models import Sequential
from keras.layers import Dense

def q_learning_nn(num_episodes, ratings):
    movies = list(set(ratings['movieId']))
    reward_dict = {0.5: -25, 1: -20, 1.5: -15, 2: -10, 2.5: -5, 3: 0, 3.5: 5, 4: 10, 4.5: 15, 5: 25}

    # One-hot encode movie IDs
    enc = OneHotEncoder()
    movie_ids_onehot = enc.fit_transform(np.array(ratings['movieId']).reshape(-1, 1))

    # Define neural network architecture
    model = Sequential()
    model.add(Dense(64, input_dim=movie_ids_onehot.shape[1], activation='relu'))
    model.add(Dense(32, activation='relu'))
    model.add(Dense(len(movies), activation='linear'))
    model.compile(loss='mse', optimizer='adam')

    gamma = 0.9
    epsilon = 0.9
    batch_size = 32

    for i in range(num_episodes):
        # Sample random observation
        observation = ratings.sample(n=1)
        terminated = False
        num_steps = 0
        prev_actions = []

        while not terminated:
            print(i, num_steps)
            num_steps += 1

            # One-hot encode current movie ID
            current_movie_onehot = enc.transform(np.array(observation['movieId']).reshape(-1, 1))

            # Predict Q-values for all actions
            q_values = model.predict(current_movie_onehot)


            pos_actions = list(set(ratings[ratings['userId']==observation['userId'].values[0]]['movieId']))
            pos_actions = [i for i in pos_actions if i not in prev_actions]

            q_val_dict = dict(zip(movies, q_values[0]))
            q_val_dict = {k: v for k, v in q_val_dict.items() if k in pos_actions}
            # Epsilon-greedy action selection
            if np.random.rand() < epsilon:
                action = np.random.choice(pos_actions)
            else:
                print(q_val_dict)
                action = max(q_val_dict, key=lambda k: q_val_dict[k])


            new_state = ratings[(ratings['userId'] == observation['userId'].values[0]) & (ratings['movieId'] == movies[action])]
            if new_state.empty:
                continue

            prev_actions += [new_state['movieId'].values[0]]

            reward = reward_dict[new_state['rating'].values[0]]  # Reward based on rating
            if reward < 10 or num_steps > 20:
                terminated = True

            # Update Q-value using Q-learning update rule
            target = reward + gamma * np.max(model.predict(enc.transform(np.array(new_state['movieId']).reshape(-1, 1))))

            # Train neural network
            model.fit(current_movie_onehot.toarray(), target.reshape(1, -1), epochs=1, batch_size=batch_size, verbose=0)

            observation = new_state


        # Update epsilon
        epsilon *= 0.999

    return model, enc


In [89]:
model, enc = q_learning_nn(1000, ratings)

c:\Users\jacob\anaconda3\envs\ds\lib\site-packages\keras\src\layers\core\dense.py:88: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


0 0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 105ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1 0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1 1
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1 2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 104ms/step
1 3
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 93ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 78ms/step
1 4
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 85ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 77ms/step
2 0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 114ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 103ms/step
3 0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 98ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 89ms/step
3 1
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 85ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 84ms/step
3 2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 104ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 104ms/step
4 0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 108ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 94ms/step
5 0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 98ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 77ms/step
6 0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 8

In [80]:
from scipy.sparse import csr_matrix

def predict_high_reward_movies(model, movie_ids, ratings, enc):
    # One-hot encode movie IDs
    movie_ids_onehot = enc.transform(np.array(movie_ids).reshape(-1, 1))

    # Convert one-hot encoded vectors to CSR format
    movie_ids_onehot_csr = csr_matrix(movie_ids_onehot)

    # Predict Q-values for the concatenated input vector
    q_values = model.predict(movie_ids_onehot_csr)

    # Get movie IDs
    movies = list(set(ratings['movieId']))

    # Create dictionary to map movie IDs to Q-values
    q_values_dict = {movie_id: q_value for movie_id, q_value in zip(movies, q_values.flatten())}

    # Sort movie IDs based on predicted Q-values (descending order)
    sorted_movie_ids = sorted(q_values_dict, key=q_values_dict.get, reverse=True)

    return sorted_movie_ids, q_values_dict




In [81]:
user_movies = [173,658,671]
print([movies[movies['movieId']==reverse_movie_dict[i]]['title'] for i in user_movies])


[257    Star Wars: Episode IV - A New Hope (1977)
Name: title, dtype: object, 1166    Star Wars: Episode V - The Empire Strikes Back...
Name: title, dtype: object, 1179    Star Wars: Episode VI - Return of the Jedi (1983)
Name: title, dtype: object]


In [90]:
recs, rec_dict = predict_high_reward_movies(model, user_movies, ratings, enc)

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 101ms/step


In [63]:
model_1, enc1 = model, enc

In [128]:
def print_top_movies(rec_dict, movies, reverse_movie_dict, top_n=10):
    rec_dict = {k: v for k, v in sorted(rec_dict.items(), key=lambda item: item[1], reverse=True)}

    for movie_id in list(rec_dict.keys())[:top_n]:
        movie_title = movies[movies['movieId'] == reverse_movie_dict[movie_id]]['title'].values[0]
        q_value = rec_dict[movie_id]
        print(f"Movie: {movie_title}, Predicted Q-value: {q_value}")

# Example usage
print_top_movies(optimal_policy, movies, reverse_movie_dict)

AttributeError: 'numpy.ndarray' object has no attribute 'items'

In [131]:
policy_dict = dict(zip(range(len(optimal_policy)), optimal_policy[:]))
policy_dict

print_top_movies(policy_dict, movies, reverse_movie_dict)

Movie: Way, Way Back, The (2013), Predicted Q-value: 3789
Movie: Apollo 13 (1995), Predicted Q-value: 3788
Movie: Underworld: Awakening (2012), Predicted Q-value: 3784
Movie: Shipping News, The (2001), Predicted Q-value: 3783
Movie: Inspector Gadget (1999), Predicted Q-value: 3780
Movie: Flintstones in Viva Rock Vegas, The (2000), Predicted Q-value: 3780
Movie: Event Horizon (1997), Predicted Q-value: 3774
Movie: Gamer (2009), Predicted Q-value: 3773
Movie: Déjà Vu (Deja Vu) (2006), Predicted Q-value: 3771
Movie: Married to the Mob (1988), Predicted Q-value: 3766


In [154]:
user_movies = [482, 239, 196]
user_movs = q2[user_movies,:]
mov = np.argmax(np.sum(user_movs, axis = 0))
print(movies[movies['movieId']== reverse_movie_dict[mov]])
print(np.max(np.sum(user_movs, axis = 0)))

    movieId                        title            genres
46       47  Seven (a.k.a. Se7en) (1995)  Mystery|Thriller
269.33417073146234


In [155]:
reverse_movie_dict = {v: k for k, v in movie_dict.items()}


In [156]:
original_movies = [reverse_movie_dict[item] for item in range(len(opt2))]
original_recs = [reverse_movie_dict[item] for item in opt2]


In [157]:
data = {'movieID': original_movies, 'recomendation': original_recs}
rec_df = pd.DataFrame(data)
rec_df.head()

movieID  recomendation
0        1            318
1        2           1203
2        3           8880
3        4            232
4        5           5319

In [116]:
movies = pd.read_csv('movies.csv')
movies.head()

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy

In [158]:
rec_df['movie name'] = rec_df.apply(lambda row: movies[movies['movieId']==row['movieID']]['title'].values[0], axis =1)
rec_df['recomendation name'] = rec_df.apply(lambda row: movies[movies['movieId']==row['recomendation']]['title'].values[0], axis =1)

In [159]:
rec_df['num_reviews'] = rec_df.apply(lambda row: by_movie[by_movie['movieId']== row['movieID']]['rating'].values[0], axis = 1)
rec_df.sort_values('num_reviews', ascending= False).head(50)

movieID  recomendation  \
239       356           3105   
211       318            858   
196       296            608   
381       593           2762   
1376     2571            527   
173       260           1196   
312       480           2300   
344       527           4226   
83        110            296   
1553     2959           1196   
378       589           1304   
658      1196           1262   
0           1            318   
2193     4993          58559   
44         50          79132   
671      1210            916   
660      1198           1193   
1499     2858           4226   
482       858           1213   
2343     5952           4973   
2533     7153              1   
42         47            296   
300       457            110   
728      1270            318   
450       780             57   
100       150            296   
389       608           1258   
31         32           4226   
1077     2028           1240   
1460     2762           2028   
1816     3578           2028   
380       592             50   
377       588            265   
245       364             50   
2050     4306            260   
260       380            110   
379       590             36   
3066    58559            318   
257       377           1219   
2029     4226          33794   
869      1580          99114   
927      1704            260   
3276    79132           4993   
698      1240           7153   
749      1291            593   
659      1197           1228   
634      1136            318   
933      1721           2019   
723      1265          48780   
227       344          31658   

                                             movie name  \
239                                 Forrest Gump (1994)   
211                    Shawshank Redemption, The (1994)   
196                                 Pulp Fiction (1994)   
381                    Silence of the Lambs, The (1991)   
1376                                 Matrix, The (1999)   
173           Star Wars: Episode IV - A New Hope (1977)   
312                                Jurassic Park (1993)   
344                             Schindler's List (1993)   
83                                    Braveheart (1995)   
1553                                  Fight Club (1999)   
378                   Terminator 2: Judgment Day (1991)   
658   Star Wars: Episode V - The Empire Strikes Back...   
0                                      Toy Story (1995)   
2193  Lord of the Rings: The Fellowship of the Ring,...   
44                           Usual Suspects, The (1995)   
671   Star Wars: Episode VI - Return of the Jedi (1983)   
660   Raiders of the Lost Ark (Indiana Jones and the...   
1499                             American Beauty (1999)   
482                               Godfather, The (1972)   
2343      Lord of the Rings: The Two Towers, The (2002)   
2533  Lord of the Rings: The Return of the King, The...   
42                          Seven (a.k.a. Se7en) (1995)   
300                                Fugitive, The (1993)   
728                           Back to the Future (1985)   
450                Independence Day (a.k.a. ID4) (1996)   
100                                    Apollo 13 (1995)   
389                                        Fargo (1996)   
31            Twelve Monkeys (a.k.a. 12 Monkeys) (1995)   
1077                         Saving Private Ryan (1998)   
1460                            Sixth Sense, The (1999)   
1816                                   Gladiator (2000)   
380                                       Batman (1989)   
377                                      Aladdin (1992)   
245                               Lion King, The (1994)   
2050                                       Shrek (2001)   
260                                    True Lies (1994)   
379                           Dances with Wolves (1990)   
3066                            Dark Knight, The (2008)   
257                                        Speed (1994)   
2029         

In [49]:
user_movies = [933, 749, 3066]
user_movs = Q[user_movies,:]
mov = np.argmax(np.sum(user_movs, axis = 0))
movies[movies['movieId']== reverse_movie_dict[mov]]

movieId            title  genres
64       65  Bio-Dome (1996)  Comedy

In [40]:
rec_df['num_reviews'] = rec_df.apply(lambda row: by_movie[by_movie['movieId']== row['movieID']]['rating'].values[0], axis = 1)
rec_df.sort_values('num_reviews', ascending= False).head(50)

movieID  recomendation  \
239       356           2918   
211       318            904   
196       296           2571   
381       593           1954   
1376     2571         103228   
173       260          59315   
312       480           3578   
344       527           1207   
83        110            527   
1553     2959           3556   
378       589            783   
658      1196           8874   
0           1           1135   
2193     4993          94959   
44         50           1178   
671      1210           4993   
660      1198           2161   
1499     2858           2761   
482       858         112290   
2343     5952            541   
2533     7153           2571   
42         47          68157   
300       457            653   
728      1270           6283   
450       780           2542   
100       150            110   
389       608           2542   
31         32          34405   
1077     2028            735   
1460     2762            592   
1816     3578           2496   
380       592            235   
377       588           2431   
245       364           5816   
2050     4306          95088   
260       380           1345   
379       590           1259   
3066    58559         152081   
257       377           1097   
2029     4226           5618   
869      1580           2406   
927      1704           4973   
3276    79132          99114   
698      1240             50   
749      1291           1483   
659      1197          99114   
634      1136           1206   
933      1721           5225   
723      1265           2692   
227       344           5418   

                                             movie name  \
239                                 Forrest Gump (1994)   
211                    Shawshank Redemption, The (1994)   
196                                 Pulp Fiction (1994)   
381                    Silence of the Lambs, The (1991)   
1376                                 Matrix, The (1999)   
173           Star Wars: Episode IV - A New Hope (1977)   
312                                Jurassic Park (1993)   
344                             Schindler's List (1993)   
83                                    Braveheart (1995)   
1553                                  Fight Club (1999)   
378                   Terminator 2: Judgment Day (1991)   
658   Star Wars: Episode V - The Empire Strikes Back...   
0                                      Toy Story (1995)   
2193  Lord of the Rings: The Fellowship of the Ring,...   
44                           Usual Suspects, The (1995)   
671   Star Wars: Episode VI - Return of the Jedi (1983)   
660   Raiders of the Lost Ark (Indiana Jones and the...   
1499                             American Beauty (1999)   
482                               Godfather, The (1972)   
2343      Lord of the Rings: The Two Towers, The (2002)   
2533  Lord of the Rings: The Return of the King, The...   
42                          Seven (a.k.a. Se7en) (1995)   
300                                Fugitive, The (1993)   
728                           Back to the Future (1985)   
450                Independence Day (a.k.a. ID4) (1996)   
100                                    Apollo 13 (1995)   
389                                        Fargo (1996)   
31            Twelve Monkeys (a.k.a. 12 Monkeys) (1995)   
1077                         Saving Private Ryan (1998)   
1460                            Sixth Sense, The (1999)   
1816                                   Gladiator (2000)   
380                                       Batman (1989)   
377                                      Aladdin (1992)   
245                               Lion King, The (1994)   
2050                                       Shrek (2001)   
260                                    True Lies (1994)   
379                           Dances with Wolves (1990)   
3066                            Dark Knight, The (2008)   
257                                        Speed (1994)   
2029         

In [31]:
df1 = pd.read_csv('movies_recs_tags_10k.csv')

df1['num_reviews'] = df1.apply(lambda row: by_movie[by_movie['movieId']== row['movieID']]['rating'].values[0], axis = 1)
df1.sort_values('num_reviews', ascending= False).head(50)

movieID  recomendation  \
239       356            356   
211       318           1172   
196       296            296   
381       593         195159   
1376     2571           2571   
173       260            260   
312       480           1090   
344       527           1059   
83        110            232   
1553     2959          56367   
378       589           3359   
658      1196          42718   
0           1           4367   
2193     4993           4993   
44         50             50   
671      1210           1210   
660      1198           1197   
1499     2858           2403   
482       858            858   
2343     5952         122926   
2533     7153           1586   
42         47             47   
300       457            457   
728      1270           1270   
450       780           2959   
100       150           6870   
389       608          64034   
31         32             32   
1077     2028           3712   
1460     2762          64716   
1816     3578           4776   
380       592           1387   
377       588            588   
245       364         112552   
2050     4306          52319   
260       380            380   
379       590            783   
3066    58559          58559   
257       377           2067   
2029     4226           5878   
869      1580           1198   
927      1704           1704   
3276    79132         165551   
698      1240           3264   
749      1291           4973   
659      1197           1197   
634      1136           1136   
933      1721            914   
723      1265          59369   
227       344           4734   

                                             movie name  \
239                                 Forrest Gump (1994)   
211                    Shawshank Redemption, The (1994)   
196                                 Pulp Fiction (1994)   
381                    Silence of the Lambs, The (1991)   
1376                                 Matrix, The (1999)   
173           Star Wars: Episode IV - A New Hope (1977)   
312                                Jurassic Park (1993)   
344                             Schindler's List (1993)   
83                                    Braveheart (1995)   
1553                                  Fight Club (1999)   
378                   Terminator 2: Judgment Day (1991)   
658   Star Wars: Episode V - The Empire Strikes Back...   
0                                      Toy Story (1995)   
2193  Lord of the Rings: The Fellowship of the Ring,...   
44                           Usual Suspects, The (1995)   
671   Star Wars: Episode VI - Return of the Jedi (1983)   
660   Raiders of the Lost Ark (Indiana Jones and the...   
1499                             American Beauty (1999)   
482                               Godfather, The (1972)   
2343      Lord of the Rings: The Two Towers, The (2002)   
2533  Lord of the Rings: The Return of the King, The...   
42                          Seven (a.k.a. Se7en) (1995)   
300                                Fugitive, The (1993)   
728                           Back to the Future (1985)   
450                Independence Day (a.k.a. ID4) (1996)   
100                                    Apollo 13 (1995)   
389                                        Fargo (1996)   
31            Twelve Monkeys (a.k.a. 12 Monkeys) (1995)   
1077                         Saving Private Ryan (1998)   
1460                            Sixth Sense, The (1999)   
1816                                   Gladiator (2000)   
380                                       Batman (1989)   
377                                      Aladdin (1992)   
245                               Lion King, The (1994)   
2050                                       Shrek (2001)   
260                                    True Lies (1994)   
379                           Dances with Wolves (1990)   
3066                            Dark Knight, The (2008)   
257                                        Speed (1994)   
2029         